In [ ]:
%matplotlib inline


# Make a S-shaped AWG

This simple example illustrates how to make an S-shaped AWG and how to run a Caphe simulation on it.
For this example, we use the IPKISS AWG Designer module.

## Getting started

We start by importing the technology with other required modules:


In [ ]:
from technologies import silicon_photonics  # noqa: F401
from ipkiss3 import all as i3
import numpy as np
import pylab as plt
import time

import awg_designer.all as awg

Template for the free propagation region
This defines the layers, slab modes, etc.



In [ ]:
slab_t = awg.SlabTemplate()
slab_t.Layout(slab_layers=[i3.PPLayer(i3.TECH.PROCESS.WG, i3.TECH.PURPOSE.DF_AREA)])
slab_t.SlabModes(modes=[awg.SimpleSlabMode(name="TE0", n_eff=2.8, n_g=3.2, polarization="TE")])

N = 44  # number of arms
R = 150.0  # radius of the star couplers
W = 2.0  # aperture width
M = 8  # outputs

## The aperture

Make virtual aperture



In [ ]:
ap = awg.OpenWireWgAperture(slab_template=slab_t)
ap_lo = ap.Layout(aperture_core_width=W, aperture_edge_width=1.0)
ap_sm = ap.FieldModelFromCamfr()
ap_cm = ap.CircuitModel(simulation_wavelengths=[1.55])

## The input star coupler

Make a multi-aperture for the arms consisting of N apertures like these, arranged in a circle
and get the transformations of the individual apertures.



In [ ]:
angle_step = i3.RAD2DEG * (W + 0.2) / R
angles_arms = np.linspace(-angle_step * (N - 1) / 2.0, angle_step * (N - 1) / 2.0, N)
ap_arms_in, _, trans_arms_in, trans_ports_in = awg.get_star_coupler_apertures(
    apertures_arms=[ap] * N,
    apertures_ports=[ap],
    angles_arms=angles_arms,
    angles_ports=[0],
    radius=R,
    mounting="confocal",
    input=True,
)

Make the input star coupler



In [ ]:
sc_in = awg.StarCoupler(aperture_in=ap, aperture_out=ap_arms_in)

sc_in_lo = sc_in.Layout(
    contour=awg.get_star_coupler_extended_contour(
        apertures_in=[ap],
        apertures_out=[ap] * N,
        trans_in=trans_ports_in,
        trans_out=trans_arms_in,
        radius_in=R,
        radius_out=R,
        extension_angles=(10, 5),
    )
)
sc_in_lo.visualize()

## The output star coupler

Make the multi-apertures for the outputs and get the transformations for the individual apertures.



In [ ]:
angle_step = i3.RAD2DEG * (4.7) / R
angles_ports = np.linspace(angle_step * (M - 1) / 2.0, -angle_step * (M - 1) / 2.0, M)
ap_arms_out, ap_out, trans_arms_out, trans_ports_out = awg.get_star_coupler_apertures(
    apertures_arms=[ap] * N,
    apertures_ports=[ap] * M,
    angles_arms=angles_arms,
    angles_ports=angles_ports,
    radius=R,
    mounting="rowland",
    input=False,
)

Make the output star coupler



In [ ]:
sc_out = awg.StarCoupler(aperture_in=ap_arms_out, aperture_out=ap_out)
sc_out_lo = sc_out.Layout(
    contour=awg.get_star_coupler_extended_contour(
        apertures_in=[ap] * N,
        apertures_out=[ap] * M,
        trans_in=trans_arms_out,
        trans_out=trans_ports_out,
        radius_in=R,
        radius_out=R / 2,
        extension_angles=(10, 10),
    )
)
sc_out_lo.visualize()

## The S shaped waveguide array

Choose the waveguide template



In [ ]:
from picazzo3.traces.wire_wg.trace import WireWaveguideTemplate  # noqa: E402

straight_tmpl = WireWaveguideTemplate()
straight_tmpl.Layout(core_width=i3.TECH.WG.WIRE_WIDTH)
straight_tmpl.CircuitModel(n_eff=2.81, n_g=4.2)

Make the SWaveguideArray



In [ ]:
delays = [10 * i for i in range(N)]
wg_array = awg.SWaveguideArray(start_ports=sc_in_lo.east_ports, end_ports=sc_out_lo.west_ports, delay_lengths=delays)
wg_array_lo = wg_array.Layout(offset_output_ports_south=15)
wg_array_lo.visualize(annotate=False)

## The Arrayed Waveguide Grating

Make an AWG with the 3 building blocks



In [ ]:
s_awg = awg.ArrayedWaveguideGrating(star_coupler_in=sc_in, star_coupler_out=sc_out, waveguide_array=wg_array)
awg_lo = s_awg.Layout()
awg_lo.visualize()

## Running the Caphe simulation



In [ ]:
print("Running Caphe simulation (with wavelength-independent star couplers)")
sc_in.CircuitModel(simulation_wavelengths=[1.55])
sc_out.CircuitModel(simulation_wavelengths=[1.55])
awg_cm = s_awg.CircuitModel()
wavelengths = np.linspace(1.52, 1.58, 401)

t0 = time.time()
S = awg_cm.get_smatrix(wavelengths)
print("Calculation time:", time.time() - t0)

for i in range(1, M + 1):
    plt.plot(wavelengths, 10 * np.log10(np.abs(S["in1", "out{}".format(i)]) ** 2), label="out{}".format(i))

plt.xlabel("wavelength")
plt.ylabel("transmission [dB]")
plt.legend()
plt.ylim([-80, 0])
plt.show()